# Лабораторная работа № 6

### Выполнил: Федоров К.С.
### Группа: Б8403а

In [5]:
import numpy as np
import pandas as pd
import scipy as sp
import matplotlib.pyplot as plt
import plotly.offline as py
import plotly.graph_objs as go
py.init_notebook_mode(connected=True)
from scipy.stats import multivariate_normal
from sklearn.cluster import KMeans
from collections import Counter
from sklearn.neighbors import KernelDensity
from sklearn.base import BaseEstimator, ClassifierMixin
from sklearn.grid_search import GridSearchCV
from scipy.spatial import ConvexHull, KDTree
from sklearn.neighbors import KNeighborsClassifier

In [144]:
# Число классов
countClasses = 3
# Число случайных величин
countVariables = 3
# Задаем объем обучающей выборки
countLearnDots = 1000
# Задаем объем контрольной выборки
countControlDots = 10000
# Выбор срезов
x1 = 0
x2 = 1
# Задаем матрицы корелляции
correlations = [
    [
        [1, 0.7, 0],
        [0.7, 1, 0],
        [0, 0, 1]
    ], [
        [1, -0.23, 0],
        [-0.23, 1, 0],
        [0, 0, 1]
    ], [
        [1, 0, 0],
        [0, 1, 0],
        [0, 0, 1]
    ]
]
# Задаем вектора дисперсии
dispersions = [
    [1.0, 3.0, 1],
    [3.0, 1.0, 1],
    [4, 3, 1]
]
# Задаем вектора средних
means = [
    [7,  -5.0, 0],
    [0.0,  -3.0,  0],
    [4.0, 4.0,  0.0]
]
# Задаем апостериорные вероятности
probabilities = [
    0.2, 0.5, 0.3
]
# Задаем коэффициенты прадоподобности
lambdas = [
    1.0, 1.0, 1.0
]
# Задаем интервалы для отрисовки поля
step = 0.1
# Задаем границы поля
x_min = -10
y_min = -10
width = 20
height = 20

In [145]:
def corToCov(cor, disp):
    cov = np.zeros((countVariables, countVariables))
    for i in range(countVariables):
        for j in range(countVariables):
            cov[i][j] = cor[i][j] * np.math.sqrt(disp[i] * disp[j])
    return cov

def generatePDF(mean, covariation):
    return np.array(list(map(multivariate_normal, mean, covariation)))
PDF_s = generatePDF(means, list(map(corToCov, correlations, dispersions)))

data_training_classes = np.random.choice(countClasses, countLearnDots, p=probabilities)
data_training_points = np.array([PDF_s[i].rvs() for i in data_training_classes])

data_control_classes = np.random.choice(countClasses, countControlDots, p=probabilities)
data_control_points = np.array([PDF_s[i].rvs() for i in data_control_classes])
# draw teaching dots
layout = go.Layout(
    width=1000,
    height=1000,
    xaxis=dict(
        range=[x_min, x_min + width]
    ),
    yaxis=dict(
        range=[y_min, y_min + width]
    )
)

data_training_points_transpose = data_training_points.transpose()
data_training_x1 = data_training_points_transpose[x1]
data_training_x2 = data_training_points_transpose[x2]
training_scatter = go.Scatter(
    x = data_training_x2,
    y = data_training_x1,
    mode = 'markers',
    name = "scatter",
    marker=dict(
        color = data_training_classes,
        colorscale=[[0.0, 'rgb(228,26,28)'], [0.25, 'rgb(55,126,184)'], [0.5, 'rgb(77,175,74)'], [0.75, 'rgb(152,78,163)'], [1.0, 'rgb(255,127,0)']],
    )
)

data_control_points_transpose = data_control_points.transpose()
data_control_x1 = data_control_points_transpose[x1]
data_control_x2 = data_control_points_transpose[x2]
control_scatter = go.Scatter(
    x = data_control_x2,
    y = data_control_x1,
    mode = 'markers',
    name = "scatter",
    marker=dict(
        color = data_control_classes,
        colorscale=[[0.0, 'rgb(228,26,28)'], [0.25, 'rgb(55,126,184)'], [0.5, 'rgb(77,175,74)'], [0.75, 'rgb(152,78,163)'], [1.0, 'rgb(255,127,0)']],
    )
)

fig_data = [training_scatter]
data = go.Figure(data = fig_data, layout = layout)
py.iplot(data)

In [128]:
def corToCov(cor, disp):
    cov = np.zeros((countVariables, countVariables))
    for i in range(countVariables):
        for j in range(countVariables):
            cov[i][j] = cor[i][j] * np.math.sqrt(disp[i] * disp[j])
    return cov

def generatePDF(mean, covariation):
    return np.array(list(map(multivariate_normal, mean, covariation)))
PDF_s = generatePDF(means, list(map(corToCov, correlations, dispersions)))

data_training_classes = np.random.choice(countClasses, countLearnDots, p=probabilities)
data_training_points = np.array([PDF_s[i].rvs() for i in data_training_classes])

data_control_classes = np.random.choice(countClasses, countControlDots, p=probabilities)
data_control_points = np.array([PDF_s[i].rvs() for i in data_control_classes])
# draw teaching dots
layout = go.Layout(
    width=1000,
    height=1000,
    xaxis=dict(
        range=[x_min, x_min + width]
    ),
    yaxis=dict(
        range=[y_min, y_min + width]
    )
)

data_training_points_transpose = data_training_points.transpose()
data_training_x1 = data_training_points_transpose[x1]
data_training_x2 = data_training_points_transpose[x2]
training_scatter = go.Scatter(
    x = data_training_x2,
    y = data_training_x1,
    mode = 'markers',
    name = "scatter",
    marker=dict(
        color = data_training_classes,
        colorscale=[[0.0, 'rgb(228,26,28)'], [0.25, 'rgb(55,126,184)'], [0.5, 'rgb(77,175,74)'], [0.75, 'rgb(152,78,163)'], [1.0, 'rgb(255,127,0)']],
    )
)

data_control_points_transpose = data_control_points.transpose()
data_control_x1 = data_control_points_transpose[x1]
data_control_x2 = data_control_points_transpose[x2]
control_scatter = go.Scatter(
    x = data_control_x2,
    y = data_control_x1,
    mode = 'markers',
    name = "scatter",
    marker=dict(
        color = data_control_classes,
        colorscale=[[0.0, 'rgb(228,26,28)'], [0.25, 'rgb(55,126,184)'], [0.5, 'rgb(77,175,74)'], [0.75, 'rgb(152,78,163)'], [1.0, 'rgb(255,127,0)']],
    )
)

fig_data = [control_scatter]
data = go.Figure(data = fig_data, layout = layout)
py.iplot(data)

In [118]:
def perfect_classifier():
    global data_control_classes
    global data_control_points
    global data_classify_classes

    def bayes(point):
        b = np.array(list(map(lambda prob, PDF_s, lambd: lambd * prob * PDF_s.pdf(point), probabilities, PDF_s, lambdas)))
        return b.argmax()

    data_classify_classes = np.array(list(map(bayes, data_control_points)))

In [119]:
def maximum_likelihood_estimation():
    global data_training_classes
    global data_training_points
    global data_control_classes
    global data_control_points
    global data_classify_classes

    c = Counter(data_training_classes)

    classes_means = {}
    for i in range(len(data_training_classes)):
        if data_training_classes[i] in classes_means:
            classes_means[data_training_classes[i]] += data_training_points[i]
        else:
            classes_means[data_training_classes[i]] = np.copy(data_training_points[i])
    for i in range(countClasses):
        classes_means[i] = classes_means[i] / c[i]
    means = np.array([classes_means[i] for i in range(countClasses)])

    classes_sigma = {}
    for i in range(len(data_training_classes)):
        if data_training_classes[i] in classes_sigma:
            classes_sigma[data_training_classes[i]] += np.dot((data_training_points[i] - means[data_training_classes[i]]), (data_training_points[i] - means[data_training_classes[i]]))
        else:
            classes_sigma[data_training_classes[i]] = np.dot((data_training_points[i] - means[data_training_classes[i]]), (data_training_points[i] - means[data_training_classes[i]]))
    for i in range(countClasses):
        classes_sigma[i] = np.sqrt(classes_sigma[i] / c[i])
    sigma = np.array([classes_sigma[i] for i in range(countClasses)])

    prob_classes = np.array([float(c[i]) / len(data_training_classes) for i in range(countClasses)])

    def bayes_m(point):
        b = np.array([np.log(lambdas[i] * prob_classes[i]) - 0.5 * np.dot((point - means[i]), (point - means[i])) * 1/sigma[i]**2 - 0.5 * np.log(np.abs(1/sigma[i])) - len(data_classify_classes)/2.0 * np.log(2*np.pi) for i in range(countClasses)])
        return b.argmax()

    data_classify_classes = np.array(list(map(bayes_m, data_control_points)))

In [120]:
def K_near_neighbours(K):
    global data_training_classes
    global data_training_points
    global data_control_classes
    global data_control_points
    global data_classify_classes

    neigh = KNeighborsClassifier(n_neighbors=K)
    neigh.fit(data_training_points, data_training_classes)
    data_classify_classes = neigh.predict(data_control_points)

In [121]:
def print_stats():
    s = ""

    global data_classify_classes
    global data_control_classes

    transform_matrix = np.zeros((countClasses, countClasses), dtype=np.int64)
    wrong_count = 0
    for i in np.arange(len(data_classify_classes)):
        class_pred = data_classify_classes[i]
        class_real = data_control_classes[i]
        wrong_count += 1 if class_real != class_pred else 0
        if (class_real >= len(transform_matrix)):
            class_real = len(transform_matrix) - 1;
        if (class_pred >= countClasses):
            class_pred = countClasses - 1;
        transform_matrix[class_real][class_pred] += 1
    wrong_prob = float(wrong_count) / len(data_classify_classes)
    return 'Оценка вероятности ошибки классификации:\n' + str(wrong_prob) + '\nМатрица трансформации(Стало\Было):\n' + np.array_str(transform_matrix.transpose())

    return s

In [122]:
data_classify_classes = np.zeros(data_control_classes.size, dtype=np.int32)
perfect_classifier()

layout = go.Layout(
    # autosize=True,
    width=1000,
    height=1000,
    xaxis=dict(
        range=[x_min, x_min + width]
    ),
    yaxis=dict(
        range=[y_min, y_min + width]
    )
)

data_training_points_transpose = data_training_points.transpose()
data_training_x1 = data_training_points_transpose[x1]
data_training_x2 = data_training_points_transpose[x2]
training_scatter = go.Scatter(
    x = data_training_x2,
    y = data_training_x1,
    # z = data_training_classes,
    mode = 'markers',
    name = "scatter",
    marker=dict(
        color = data_training_classes,
        # color = data_training_classes if gr_type == "real" else data_classify_classes,
        # colorscale=[[0, 'rgb(228,26,28)'], [0.5, 'rgb(55,126,184)'], [1.0, 'rgb(77,175,74)']],
        colorscale=[[0.0, 'rgb(228,26,28)'], [0.25, 'rgb(55,126,184)'], [0.5, 'rgb(77,175,74)'], [0.75, 'rgb(152,78,163)'], [1.0, 'rgb(255,127,0)']],
        # showscale=True,
    )
)

data_control_points_transpose = data_control_points.transpose()
data_control_x1 = data_control_points_transpose[x1]
data_control_x2 = data_control_points_transpose[x2]
control_scatter = go.Scatter(
    x = data_control_x2,
    y = data_control_x1,
    mode = 'markers',
    name = "scatter",
    marker=dict(
        # color = data_control_classes,
        color = data_classify_classes,
        # colorscale=[[0, 'rgb(228,26,28)'], [0.5, 'rgb(55,126,184)'], [1.0, 'rgb(77,175,74)']],
        colorscale=[[0.0, 'rgb(228,26,28)'], [0.25, 'rgb(55,126,184)'], [0.5, 'rgb(77,175,74)'], [0.75, 'rgb(152,78,163)'], [1.0, 'rgb(255,127,0)']],
    )
)


first_wrong = True
for i in range(len(data_classify_classes)):
    if (data_classify_classes[i] != data_control_classes[i]):
        if first_wrong:
            wrong_points = np.array([data_control_points[i]])
            first_wrong = False
        else:
            wrong_points = np.append(wrong_points, [data_control_points[i]], axis=0)
    # print(wrong_points)
data_wrong_points_transpose = wrong_points.transpose()
data_wrong_x1 = data_wrong_points_transpose[x1]
data_wrong_x2 = data_wrong_points_transpose[x2]
# data_control_classes if gr_type == "real" else 
# if gr_type == "real":
data_wrong_x1 = np.array(0)
data_wrong_x2 = np.array(0)
# 


wrong_scatter = go.Scatter(
    x = data_wrong_x2,
    y = data_wrong_x1,
    mode = 'markers',
    name = "scatter",
    marker=dict(
        color = 'rgb(0,0,0)',
        # color = data_control_classes if gr_type == "real" else data_classify_classes,
        # colorscale=[[0, 'rgb(228,26,28)'], [0.5, 'rgb(55,126,184)'], [1.0, 'rgb(77,175,74)']],
        # colorscale=[[0.0, 'rgb(0,0,0)'], [1.0, 'rgb(0,0,0)']],
    )
)

fig_data = [training_scatter, control_scatter, wrong_scatter]
# fig_data = [training_scatter]
# fig_data = [control_scatter, wrong_scatter]

data = go.Figure(data = fig_data, layout = layout)
py.iplot(data)
print(print_stats())

Оценка вероятности ошибки классификации:
0.0032
Матрица трансформации(Стало\Было):
[[2029    7    3]
 [   1 4856   14]
 [   1    6 3083]]


In [123]:
data_classify_classes = np.zeros(data_control_classes.size, dtype=np.int32)
maximum_likelihood_estimation()

layout = go.Layout(
    # autosize=True,
    width=1000,
    height=1000,
    xaxis=dict(
        range=[x_min, x_min + width]
    ),
    yaxis=dict(
        range=[y_min, y_min + width]
    )
)

data_training_points_transpose = data_training_points.transpose()
data_training_x1 = data_training_points_transpose[x1]
data_training_x2 = data_training_points_transpose[x2]
training_scatter = go.Scatter(
    x = data_training_x2,
    y = data_training_x1,
    # z = data_training_classes,
    mode = 'markers',
    name = "scatter",
    marker=dict(
        color = data_training_classes,
        # color = data_training_classes if gr_type == "real" else data_classify_classes,
        # colorscale=[[0, 'rgb(228,26,28)'], [0.5, 'rgb(55,126,184)'], [1.0, 'rgb(77,175,74)']],
        colorscale=[[0.0, 'rgb(228,26,28)'], [0.25, 'rgb(55,126,184)'], [0.5, 'rgb(77,175,74)'], [0.75, 'rgb(152,78,163)'], [1.0, 'rgb(255,127,0)']],
        # showscale=True,
    )
)

data_control_points_transpose = data_control_points.transpose()
data_control_x1 = data_control_points_transpose[x1]
data_control_x2 = data_control_points_transpose[x2]
control_scatter = go.Scatter(
    x = data_control_x2,
    y = data_control_x1,
    mode = 'markers',
    name = "scatter",
    marker=dict(
        # color = data_control_classes,
        color = data_classify_classes,
        # colorscale=[[0, 'rgb(228,26,28)'], [0.5, 'rgb(55,126,184)'], [1.0, 'rgb(77,175,74)']],
        colorscale=[[0.0, 'rgb(228,26,28)'], [0.25, 'rgb(55,126,184)'], [0.5, 'rgb(77,175,74)'], [0.75, 'rgb(152,78,163)'], [1.0, 'rgb(255,127,0)']],
    )
)


first_wrong = True
for i in range(len(data_classify_classes)):
    if (data_classify_classes[i] != data_control_classes[i]):
        if first_wrong:
            wrong_points = np.array([data_control_points[i]])
            first_wrong = False
        else:
            wrong_points = np.append(wrong_points, [data_control_points[i]], axis=0)
    # print(wrong_points)
data_wrong_points_transpose = wrong_points.transpose()
data_wrong_x1 = data_wrong_points_transpose[x1]
data_wrong_x2 = data_wrong_points_transpose[x2]
# data_control_classes if gr_type == "real" else 
# if gr_type == "real":
data_wrong_x1 = np.array(0)
data_wrong_x2 = np.array(0)
# 


wrong_scatter = go.Scatter(
    x = data_wrong_x2,
    y = data_wrong_x1,
    mode = 'markers',
    name = "scatter",
    marker=dict(
        color = 'rgb(0,0,0)',
        # color = data_control_classes if gr_type == "real" else data_classify_classes,
        # colorscale=[[0, 'rgb(228,26,28)'], [0.5, 'rgb(55,126,184)'], [1.0, 'rgb(77,175,74)']],
        # colorscale=[[0.0, 'rgb(0,0,0)'], [1.0, 'rgb(0,0,0)']],
    )
)

fig_data = [training_scatter, control_scatter, wrong_scatter]
# fig_data = [training_scatter]
# fig_data = [control_scatter, wrong_scatter]

data = go.Figure(data = fig_data, layout = layout)
py.iplot(data)
print(print_stats())

Оценка вероятности ошибки классификации:
0.0082
Матрица трансформации(Стало\Было):
[[2019   33    1]
 [   0 4834   34]
 [  12    2 3065]]


In [146]:
data_classify_classes = np.zeros(data_control_classes.size, dtype=np.int32)

def near_neighbours(alpha):
    global data_training_classes
    global data_training_points
    global data_control_classes
    global data_control_points
    global data_classify_classes

    classesToPoints = {}
    for i in range(len(data_training_points)):
        if data_training_classes[i] in classesToPoints:
            classesToPoints[data_training_classes[i]] = np.append(classesToPoints[data_training_classes[i]], [data_training_points[i]], axis=0)
        else:
            classesToPoints[data_training_classes[i]] = np.array([data_training_points[i]])

    classesToTree = {}
    for i in range(countClasses):
        classesToTree[i] = KDTree(classesToPoints[i])

    k_n = np.sqrt(len(data_training_classes))*alpha

    c = Counter(data_training_classes)
    prob_classes = np.array([float(c[i]) / len(data_training_classes) for i in range(countClasses)])

    def pdf_k(point, i):
        dist, indexes = classesToTree[i].query([point], k = int(k_n))
        con_hul = ConvexHull(np.take(classesToPoints[i], indexes[0], axis=0))
        return 1.0/con_hul.volume

    def bayes_k(point):
        b = np.array([lambdas[i] * prob_classes[i] * pdf_k(point, i) for i in range(countClasses)])
        return b.argmin()

    data_classify_classes = np.array(list(map(bayes_k, data_control_points)))

near_neighbours(1)

layout = go.Layout(
    # autosize=True,
    width=1000,
    height=1000,
    xaxis=dict(
        range=[x_min, x_min + width]
    ),
    yaxis=dict(
        range=[y_min, y_min + width]
    )
)

data_training_points_transpose = data_training_points.transpose()
data_training_x1 = data_training_points_transpose[x1]
data_training_x2 = data_training_points_transpose[x2]
training_scatter = go.Scatter(
    x = data_training_x2,
    y = data_training_x1,
    # z = data_training_classes,
    mode = 'markers',
    name = "scatter",
    marker=dict(
        color = data_training_classes,
        # color = data_training_classes if gr_type == "real" else data_classify_classes,
        # colorscale=[[0, 'rgb(228,26,28)'], [0.5, 'rgb(55,126,184)'], [1.0, 'rgb(77,175,74)']],
        colorscale=[[0.0, 'rgb(228,26,28)'], [0.25, 'rgb(55,126,184)'], [0.5, 'rgb(77,175,74)'], [0.75, 'rgb(152,78,163)'], [1.0, 'rgb(255,127,0)']],
        # showscale=True,
    )
)

data_control_points_transpose = data_control_points.transpose()
data_control_x1 = data_control_points_transpose[x1]
data_control_x2 = data_control_points_transpose[x2]
control_scatter = go.Scatter(
    x = data_control_x2,
    y = data_control_x1,
    mode = 'markers',
    name = "scatter",
    marker=dict(
        # color = data_control_classes,
        color = data_classify_classes,
        # colorscale=[[0, 'rgb(228,26,28)'], [0.5, 'rgb(55,126,184)'], [1.0, 'rgb(77,175,74)']],
        colorscale=[[0.0, 'rgb(228,26,28)'], [0.25, 'rgb(55,126,184)'], [0.5, 'rgb(77,175,74)'], [0.75, 'rgb(152,78,163)'], [1.0, 'rgb(255,127,0)']],
    )
)


first_wrong = True
for i in range(len(data_classify_classes)):
    if (data_classify_classes[i] != data_control_classes[i]):
        if first_wrong:
            wrong_points = np.array([data_control_points[i]])
            first_wrong = False
        else:
            wrong_points = np.append(wrong_points, [data_control_points[i]], axis=0)
    # print(wrong_points)
data_wrong_points_transpose = wrong_points.transpose()
data_wrong_x1 = data_wrong_points_transpose[x1]
data_wrong_x2 = data_wrong_points_transpose[x2]
# data_control_classes if gr_type == "real" else 
# if gr_type == "real":
data_wrong_x1 = np.array(0)
data_wrong_x2 = np.array(0)
# 


wrong_scatter = go.Scatter(
    x = data_wrong_x2,
    y = data_wrong_x1,
    mode = 'markers',
    name = "scatter",
    marker=dict(
        color = 'rgb(0,0,0)',
        # color = data_control_classes if gr_type == "real" else data_classify_classes,
        # colorscale=[[0, 'rgb(228,26,28)'], [0.5, 'rgb(55,126,184)'], [1.0, 'rgb(77,175,74)']],
        # colorscale=[[0.0, 'rgb(0,0,0)'], [1.0, 'rgb(0,0,0)']],
    )
)

# fig_data = [training_scatter, control_scatter, wrong_scatter]
# fig_data = [training_scatter]
fig_data = [control_scatter, wrong_scatter]

data = go.Figure(data = fig_data, layout = layout)
py.iplot(data)
print(print_stats())

Оценка вероятности ошибки классификации:
0.9402
Матрица трансформации(Стало\Было):
[[   0    0 2451]
 [   0    0    0]
 [1992 4959  598]]


In [112]:
data_classify_classes = np.zeros(data_control_classes.size, dtype=np.int32)
K_near_neighbours(3)

layout = go.Layout(
    # autosize=True,
    width=1000,
    height=1000,
    xaxis=dict(
        range=[x_min, x_min + width]
    ),
    yaxis=dict(
        range=[y_min, y_min + width]
    )
)

data_training_points_transpose = data_training_points.transpose()
data_training_x1 = data_training_points_transpose[x1]
data_training_x2 = data_training_points_transpose[x2]
training_scatter = go.Scatter(
    x = data_training_x2,
    y = data_training_x1,
    # z = data_training_classes,
    mode = 'markers',
    name = "scatter",
    marker=dict(
        color = data_training_classes,
        # color = data_training_classes if gr_type == "real" else data_classify_classes,
        # colorscale=[[0, 'rgb(228,26,28)'], [0.5, 'rgb(55,126,184)'], [1.0, 'rgb(77,175,74)']],
        colorscale=[[0.0, 'rgb(228,26,28)'], [0.25, 'rgb(55,126,184)'], [0.5, 'rgb(77,175,74)'], [0.75, 'rgb(152,78,163)'], [1.0, 'rgb(255,127,0)']],
        # showscale=True,
    )
)

data_control_points_transpose = data_control_points.transpose()
data_control_x1 = data_control_points_transpose[x1]
data_control_x2 = data_control_points_transpose[x2]
control_scatter = go.Scatter(
    x = data_control_x2,
    y = data_control_x1,
    mode = 'markers',
    name = "scatter",
    marker=dict(
        # color = data_control_classes,
        color = data_classify_classes,
        # colorscale=[[0, 'rgb(228,26,28)'], [0.5, 'rgb(55,126,184)'], [1.0, 'rgb(77,175,74)']],
        colorscale=[[0.0, 'rgb(228,26,28)'], [0.25, 'rgb(55,126,184)'], [0.5, 'rgb(77,175,74)'], [0.75, 'rgb(152,78,163)'], [1.0, 'rgb(255,127,0)']],
    )
)


first_wrong = True
for i in range(len(data_classify_classes)):
    if (data_classify_classes[i] != data_control_classes[i]):
        if first_wrong:
            wrong_points = np.array([data_control_points[i]])
            first_wrong = False
        else:
            wrong_points = np.append(wrong_points, [data_control_points[i]], axis=0)
    # print(wrong_points)
data_wrong_points_transpose = wrong_points.transpose()
data_wrong_x1 = data_wrong_points_transpose[x1]
data_wrong_x2 = data_wrong_points_transpose[x2]
# data_control_classes if gr_type == "real" else 
# if gr_type == "real":
data_wrong_x1 = np.array(0)
data_wrong_x2 = np.array(0)
# 


wrong_scatter = go.Scatter(
    x = data_wrong_x2,
    y = data_wrong_x1,
    mode = 'markers',
    name = "scatter",
    marker=dict(
        color = 'rgb(0,0,0)',
        # color = data_control_classes if gr_type == "real" else data_classify_classes,
        # colorscale=[[0, 'rgb(228,26,28)'], [0.5, 'rgb(55,126,184)'], [1.0, 'rgb(77,175,74)']],
        # colorscale=[[0.0, 'rgb(0,0,0)'], [1.0, 'rgb(0,0,0)']],
    )
)

fig_data = [training_scatter, control_scatter, wrong_scatter]
# fig_data = [training_scatter]
# fig_data = [control_scatter, wrong_scatter]

data = go.Figure(data = fig_data, layout = layout)
py.iplot(data)
print(print_stats())

Оценка вероятности ошибки классификации:
0.123
Матрица трансформации(Стало\Было):
[[1800    3  536]
 [  11 4808  279]
 [ 235  166 2162]]
